<a href="https://colab.research.google.com/github/fcm1006/CUHK/blob/GISM/GeoSpatialBigData%20/%20Tutorial_4.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 1 Past contents

## 1.1 Last lab: DBscan
we tried to use clustering to group up the "big data" into fewer clusters and measure the network relation.
<img src="https://miro.medium.com/proxy/1*tc8UF-h0nQqUfLC8-0uInQ.gif"/>

----------------------------

## 1.2 Last lecture: Spatial Index
https://drive.google.com/file/d/1ddacZzF2c_xr_Q1h8po5krwodqdtONF7/view?usp=share_link


# 2 This lab: Spatial index for query tutorial

Geospatial query in ArcGIS:

1. Intersect
2. Are within a distance of
3. Contains
4. Are within
5. Have a boundary that touches
6. Share a line segment with
7. Are crossed by the outline of


<img src="https://pygis.io/_images/overlay_contains.jpg"/>
<img src="https://pygis.io/_images/overlay_crosses.jpg"/>



<img src="https://samim.io/static/upload/Webp.net-compress-image107.jpg"/>




**Do we need to measure the relationship among those distant object?**

-- Focus on the objects close to each other. 

Spatial index helps to **filter** those close spatial objects when managing big data

## 2.1 Explor the data

In [ ]:
# read the coordinate data

import pandas as pd

k_df = pd.read_csv('https://raw.githubusercontent.com/gyshion/tutorial/main/K.csv')
print("k_df' size: ",len(k_df))

m_df = pd.read_csv('https://raw.githubusercontent.com/gyshion/tutorial/main/M.csv')
print("√' size: ",len(m_df))

food_df = pd.read_csv('https://github.com/gyshion/tutorial/raw/main/restaurants.zip')
print("food_df' size: ",len(food_df))

In [ ]:
print(m_df)
print(k_df)
print(food_df)


## 2.2 Plot some subset data

In [ ]:
!pip install folium

import folium
gaode = 'http://wprd03.is.autonavi.com/appmaptile?style=7&x={x}&y={y}&z={z}' 

In [ ]:
import random

plot_km = folium.Map(tiles=gaode,
                      location=[30, 100],
                      zoom_start = 4,
                      attr = 'plot_k&m')

for _, row in k_df.iterrows():
  if random.random()<0.1: # 1/10 sample
    continue
  folium.CircleMarker(
      [row['y'],row['x']],
      radius=2,
      color = '#ff6666' # red
      ).add_to(plot_km)


for _, row in m_df.iterrows():
  if random.random()<0.1: # 1/10 sample
    continue
  folium.CircleMarker(
      [row['y'],row['x']],
      radius=2,
      color = '#6666ff' # blue
      ).add_to(plot_km)

plot_km

In [ ]:
food_df_sample = food_df.sample(n=2000) # randomly sample 2000

plot_food = folium.Map(tiles=gaode,
                      location=[30, 100],
                      zoom_start = 4,
                      attr = 'plot_food')

for _, row in food_df_sample.iterrows():
  folium.CircleMarker(
      [row['y'],row['x']],
      radius=2,
      color = '#66ff66' # green
      ).add_to(plot_food)

plot_food

## 2.3 Task: Plot KFC stores located where no Mcdonald's within 10km 



In [ ]:
!pip install haversine

In [ ]:
from haversine import haversine_vector, Unit
import numpy as np

hk = (22.28, 114.17) # (lat, lon)
sh = (31.22, 121.48)
sz = (22.54, 114.05)

dist_matrix = haversine_vector([hk], [sz, sh], Unit.KILOMETERS, comb=True)

print(dist_matrix)

[[  31.43245281]
 [1230.05018129]]


In [ ]:
# work out the distance matrix of M and K

m_coors = list(m_df[['y','x']].itertuples(index=False, name=None))
print(m_coors)

# finish by yourself and get the pair-wise distance matrix of M and K
k_coors = list(k_df[['y','x']].itertuples(index=False, name=None))
dist_matrix = haversine_vector(k_coors, m_coors, Unit.KILOMETERS, comb=True)


[(39.760626, 116.545541), (23.151973, 113.35327), (26.220934, 104.100253), (31.11456, 121.569551), (31.286, 121.492465), (33.604092, 119.03303), (31.229455, 121.428243), (32.304662, 118.312373), (20.01452, 110.255812), (30.561761, 114.210543), (28.208926, 112.997012), (22.710246, 114.236637), (26.076494, 119.275014), (31.183271, 121.426965), (22.522853, 113.939902), (31.265272, 120.746794), (29.57202, 106.570565), (36.661131, 116.997127), (25.249082, 110.21354), (39.753771, 116.998414), (30.58203, 114.289313), (33.075489, 107.025781), (21.868621, 111.997435), (32.020014, 118.830072), (39.136574, 117.187543), (25.955382, 119.261513), (40.046573, 113.365535), (30.68558, 103.862877), (18.277852, 109.512053), (33.739999, 113.309818), (23.040036, 113.110348), (39.185959, 117.201846), (24.820442, 118.573152), (31.590623, 120.308474), (38.938221, 121.578492), (24.931725, 118.476101), (37.824704, 112.583283), (30.241063, 120.012653), (35.234502, 115.465006), (24.506814, 118.13147), (31.238655,

In [ ]:
dist_matrix.shape

(3414, 8374)

In [ ]:
K_min_dist_to_M = np.min(dist_matrix, axis=0)
K_min_dist_to_M.shape

(8374,)

In [ ]:
K_min_dist_to_M

array([ 3.70920984, 38.70071487,  0.16138661, ..., 19.4825641 ,
        4.48971624,  0.10588054])

In [ ]:
# method 1
plot_1 = folium.Map(tiles=gaode,
                      location=[30, 100],
                      zoom_start = 4,
                      attr = 'plot_1')

for index, row in m_df.iterrows():
  folium.CircleMarker(
      [row['y'],row['x']],
      radius=2,
      color = '#6666ff' # blue
      ).add_to(plot_1)


for index, row in k_df.iterrows():
  if K_min_dist_to_M[index]>=10:
    folium.CircleMarker(
        [row['y'],row['x']],
        radius=2,
        color = '#ff6666' # red
        ).add_to(plot_1)

plot_1



## 2.4 Estimate the variable size

In [ ]:
import sys

'''
1 KilloByte == 1024 Bytes
1 Megabyte == 1024*1024 Bytes
1 GigaByte == 1024*1024*1024 Bytes
'''

mk = len(k_df) * len(m_df) # shape of K_min_dist_to_M
var_size = sys.getsizeof(K_min_dist_to_M)/(1024*1024)
print(var_size, 'MB')

0.063995361328125 MB


In [ ]:
# estimate the size of distance matrix if we calculate the pair-wise distance of food and food

food_food = len(food_df) * len(food_df)

var_size/mk*food_food # 10 GB

10152.699747725066



<img src="https://techcult.com/wp-content/uploads/2016/03/your-computer-is-low-on-memory-fix.png"/>

## 2.5 H3 spatial index system
https://www.uber.com/en-HK/blog/h3/

In [ ]:
!pip install h3
import h3

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
for i in range(10):
  print('Level',i,":",h3.edge_length(i, unit='km'))

Level 0 : 1107.712591
Level 1 : 418.6760055
Level 2 : 158.2446558
Level 3 : 59.81085794
Level 4 : 22.6063794
Level 5 : 8.544408276
Level 6 : 3.229482772
Level 7 : 1.220629759
Level 8 : 0.461354684
Level 9 : 0.174375668


In [ ]:
lat = 30
lng = 120
res = 4

h3_code = h3.geo_to_h3(lat, lng, res)
print(h3_code)

8441967ffffffff


In [ ]:
k = 1
h3ring = h3.k_ring(h3_code, k)
h3ring

{'84309a5ffffffff',
 '8441929ffffffff',
 '844192dffffffff',
 '8441961ffffffff',
 '8441963ffffffff',
 '8441965ffffffff',
 '8441967ffffffff'}

## 2.6 Plot the H3 grid

In [ ]:

def visualize_hexagons(hexagons, color="red", folium_map=None):
    """
    hexagons is a list of hexcluster. Each hexcluster is a list of hexagons. 
    eg. [[hex1, hex2], [hex3, hex4]]
    """
    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        # flatten polygons into loops.
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v:v[0],polyline))
        lng.extend(map(lambda v:v[1],polyline))
        polylines.append(polyline)
    
    if folium_map is None:
        m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
    else:
        m = folium_map
    for polyline in polylines:
        my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color=color)
        m.add_child(my_PolyLine)
    return m
    

def visualize_polygon(polyline, color):
    polyline.append(polyline[0])
    lat = [p[0] for p in polyline]
    lng = [p[1] for p in polyline]
    m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
    my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color=color)
    m.add_child(my_PolyLine)
    return m

In [ ]:
                                                                                               
m = visualize_hexagons(list(h3ring))
display(m)

## 2.7 Query by spatial index

In [ ]:
k_df['h3'] = k_df.apply(lambda row: h3.geo_to_h3(row['y'], row['y'], 4), axis=1)
k_df

x          y               h3
0     115.649940  37.740271  842dad7ffffffff
1     115.663431  23.299871  843ef49ffffffff
2     108.910435  34.156991  842da65ffffffff
3     114.071229  22.541785  843ef69ffffffff
4     113.916093  22.484059  843ef69ffffffff
...          ...        ...              ...
8369  120.296590  31.524483  843e641ffffffff
8370  117.684038  36.222039  842da17ffffffff
8371  118.380128  33.773766  843f49bffffffff
8372  114.014902  22.730921  843ea93ffffffff
8373  120.181503  35.969310  842da17ffffffff

[8374 rows x 3 columns]

In [ ]:
m_df['h3'] = m_df.apply(lambda row: h3.geo_to_h3(row['y'], row['y'], 4), axis=1)
m_df

x          y               h3
0     116.545541  39.760626  842d1b3ffffffff
1     113.353270  23.151973  843ef4dffffffff
2     104.100253  26.220934  843e0bdffffffff
3     121.569551  31.114560  843e66bffffffff
4     121.492465  31.286000  843e647ffffffff
...          ...        ...              ...
3409  123.210407  41.258786  842c201ffffffff
3410  104.078769  30.655692  843e661ffffffff
3411  121.738282  31.063335  843e66bffffffff
3412  104.919100  25.103248  843e191ffffffff
3413  116.413343  39.915075  842d1b3ffffffff

[3414 rows x 3 columns]

In [ ]:
m_h3_lst = m_df.groupby(['h3']).apply(lambda df: list(zip(df.y, df.x))).to_dict()

m_h3_lst

{'8410939ffffffff': [(49.599763, 117.42936)],
 '841093dffffffff': [(49.210381, 119.768482)],
 '842c201ffffffff': [(41.106661, 123.058328),
  (41.290182, 123.76203),
  (41.113687, 122.990648),
  (41.131865, 122.088451),
  (41.112211, 122.993323),
  (41.117363, 121.140109),
  (41.262684, 123.173361),
  (41.102375, 122.993945),
  (41.116192, 122.095143),
  (41.293915, 123.762269),
  (41.258786, 123.210407)],
 '842c203ffffffff': [(41.576693, 120.452881), (41.633053, 123.493754)],
 '842c205ffffffff': [(40.832063, 111.609393),
  (40.817813, 111.668774),
  (40.965323, 117.954493),
  (40.969722, 117.941485),
  (40.830982, 111.710554),
  (40.815554, 111.669261),
  (40.820175, 111.733293),
  (40.811529, 111.665168),
  (40.816852, 114.882653),
  (40.972087, 117.937838),
  (40.827775, 111.697181),
  (40.980267, 117.9444),
  (40.859361, 122.749822),
  (40.849342, 111.765878),
  (40.797245, 111.561685)],
 '842c211ffffffff': [(41.868792, 123.41684),
  (41.863534, 123.904384),
  (41.851484, 123.358514

# 3 Assignment
<img src="https://i.pinimg.com/originals/89/56/79/89567940af66fb3134bcc3f60f8cb8f2.jpg"/>




*   Store num of KFC: 8374
*   Store num of Mcdonald's: 3414
*   Other food stores: ~ 2 million




The Mcdonald's plans to follow KFC and establishs the new branches with the conditions:
1. Next to current KFC store (print the coordinates of KFC stores at last)
2. No existing Mcdonald's store within 10km
3. More than 100 other food stores within 500m

Tips:
* Use H3 index
* Carefully select the resolution/level of h3

